# Install Packages

In [ ]:
%pip install jaxtyping transformer_lens plotly-utils einops torch sae_lens
%pip install numpy==1.23.5
%pip install gensim
%pip install git+https://github.com/callummcdougall/eindex.git

# Import Packages

In [12]:
import os
os.environ['KMP_DUPLICATE_LIB_OK'] = 'TRUE'
import torch as t
from torch import nn, Tensor
from torch.distributions.categorical import Categorical
from torch.nn import functional as F
from dataclasses import dataclass
import numpy as np
import einops
from jaxtyping import Float, Int
from typing import Optional, Callable, Union, List, Tuple
from functools import partial
from tqdm.notebook import tqdm
from dataclasses import dataclass
from rich import print as rprint
from rich.table import Table
from IPython.display import display, HTML
from pathlib import Path
from sae_lens import SAE
import plotly.express as px

from transformer_lens import HookedTransformer, FactoredMatrix
from transformer_lens.hook_points import HookPoint
from transformer_lens.utils import (
    load_dataset,
    tokenize_and_concatenate,
    download_file_from_hf,
)
# from plotly_utils import imshow, line, hist

device = (
    "cuda"
    if t.cuda.is_available()
    else "mps"
    if t.backends.mps.is_available()
    else "cpu"
)

print("Using device:", device)

MAIN = __name__ == "__main__"

python(42458) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
python(42459) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.


Using device: mps


# Coherence Score Analysis

## Load Models

First load the pretrained transformer and SAE:

In [2]:
model = HookedTransformer.from_pretrained("gpt2-small").to(device)

Loaded pretrained model gpt2-small into HookedTransformer
Moving model to device:  mps


In [3]:
sae, cfg_dict, sparsity = SAE.from_pretrained(release="gpt2-small-res-jb", sae_id="blocks.8.hook_resid_pre")

Next load the fine-tuned transformer and custom SAE:

In [6]:
path_to_custom_transformer_dict = '../models/fine-tuned/fine_tuned_gpt2/model.safetensors'

from safetensors import safe_open

# Initialize the HookedTransformer with the same architecture as your fine-tuned model
custom_model = HookedTransformer.from_pretrained("gpt2")  # base model

# Load the state dict from the .safetensors file
with safe_open(path_to_custom_transformer_dict, framework="pt", device=device) as f:
    state_dict = {key: f.get_tensor(key) for key in f.keys()}

# Load the state dict into the model
custom_model.load_state_dict(state_dict, strict=False)

custom_model = model.to(device)

Loaded pretrained model gpt2 into HookedTransformer
Moving model to device:  mps


In [5]:
path_to_custom_sae_dict = '../models/sae/gpt2-small-fine-tuned-layer-8'
custom_sae = SAE.load_from_pretrained(path_to_custom_sae_dict, device=device)

## Load Word Embeddings

In [12]:
import gensim.downloader as api

# Load word embeddings
print("Loading GloVe embeddings...")
word_embeddings = api.load("glove-wiki-gigaword-100")
print("GloVe embeddings loaded.")

Loading GloVe embeddings...
[==================================================] 100.0% 128.1/128.1MB downloaded
GloVe embeddings loaded.


## Define Functions

In [14]:
from sae_lens.analysis.feature_statistics import get_W_U_W_dec_stats_df
from tqdm import tqdm
from typing import Dict, List, Tuple
from torch import Tensor, topk
from scipy.spatial.distance import cosine


def calculate_coherence_stats(feature_summaries, feature_ids=None):
    if feature_ids is None:
        coherence_scores = [summary['coherence_score'] for summary in feature_summaries.values()]
    else:
        coherence_scores = [feature_summaries[i]['coherence_score'] for i in feature_ids if i in feature_summaries]
    
    coherence_scores = np.array(coherence_scores)
    non_zero_scores = coherence_scores[coherence_scores > 0]
    
    stats = {
        "mean_all": np.mean(coherence_scores),
        "median_all": np.median(coherence_scores),
        "mean_non_zero": np.mean(non_zero_scores) if len(non_zero_scores) > 0 else 0,
        "median_non_zero": np.median(non_zero_scores) if len(non_zero_scores) > 0 else 0,
        "fraction_non_zero": len(non_zero_scores) / len(coherence_scores),
    }
    
    return stats

def semantic_coherence_score(activated_tokens, activation_scores, word_embeddings):
    tokens_and_scores = [(t.lower(), score) for t, score in zip(activated_tokens, activation_scores) if t.lower().isalpha()]

    token_embeddings = []
    weights = []
    for token, score in tokens_and_scores:
        if token in word_embeddings:
            token_embeddings.append(word_embeddings[token])
            weights.append(score)

    similarities = []
    total_weight = 0
    for i in range(len(token_embeddings)):
        for j in range(i+1, len(token_embeddings)):
            sim = 1 - cosine(token_embeddings[i], token_embeddings[j])
            weight = weights[i] * weights[j]
            similarities.append(sim * weight)
            total_weight += weight

    return np.sum(similarities) / total_weight if total_weight > 0 else 0

def get_top_k_words(
    feature_activations: Tensor, words: List[str], k: int = 10
) -> List[Tuple[str, float]]:
    """
    Get the top k activated words for a given feature.

    Args:
        feature_activations (torch.Tensor): Activation values for a feature.
        words (List[str]): List of words in the vocabulary.
        k (int): Number of top words to return.

    Returns:
        List[Tuple[str, float]]: List of tuples containing top words and their activation values.
    """
    if feature_activations.numel() == 0:
        return []

    k = min(k, feature_activations.numel())
    top_k_values, top_k_indices = topk(feature_activations, k)
    top_k_words = [words[i] for i in top_k_indices.tolist()]
    top_k_activations = top_k_values.tolist()

    return list(zip(top_k_words, top_k_activations))

def get_feature_summaries(sae, word_embeddings):
    # Assuming W_dec, model, and other necessary variables are already defined
    W_dec = sae.W_dec.detach().cpu()
    W_U_stats_df_dec, dec_projection_onto_W_U = get_W_U_W_dec_stats_df(
        W_dec, model, cosine_sim=False
    )

    number_of_features = dec_projection_onto_W_U.shape[0]

    # Get vocabulary
    vocab = model.tokenizer.get_vocab()
    words = sorted(vocab.keys(), key=lambda x: vocab[x])

    feature_summaries = {}
    for i in tqdm(range(number_of_features), desc="Processing features"):
        feature_activations = dec_projection_onto_W_U[i]
        top_activated_words = get_top_k_words(feature_activations, words)

        activated_tokens, activation_scores = zip(*top_activated_words)

        coherence_score = semantic_coherence_score(activated_tokens, activation_scores, word_embeddings)
        feature_summary = {
            "feature_idx": i,
            "top_activated_words": top_activated_words,
            "activation_scores": activation_scores,
            "coherence_score": coherence_score
        }
        feature_summaries[i] = feature_summary
    
    return feature_summaries

## Compute Feature Summaries

In [15]:
baseline_feature_summaries = get_feature_summaries(sae, word_embeddings)
finetuned_feature_summaries = get_feature_summaries(custom_sae, word_embeddings)

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
Processing features:   0%|          | 0/24576 [00:00<?, ?it/s]To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
Processing features: 100%|██████████| 24576/24576 [00:27<00:00, 906.09it/s] 


## Get the Feature IDs

In [16]:
import json
import pandas as pd

path_to_parsed_features = '../features/parsed_features.json'

# Load the JSON data
with open(path_to_parsed_features, 'r') as f:
    data = json.load(f)

# Function to convert the nested dictionary to a DataFrame
def dict_to_df(data_dict):
    rows = []
    for feature, tokens in data_dict.items():
        for token, activation in tokens.items():
            rows.append({
                'feature': int(feature),
                'token': token,
                'activation': activation
            })
    return pd.DataFrame(rows)

# Create DataFrames for baseline and finetuned data
baseline_df = dict_to_df(data['baseline'])
finetuned_df = dict_to_df(data['finetuned'])

baseline_feature_ids = baseline_df.feature.unique()
finetuned_feature_ids = finetuned_df.feature.unique()

## Compute Coherence Score Stats!

In [19]:
# Calculate stats for both models
baseline_stats = calculate_coherence_stats(baseline_feature_summaries)
baseline_medical_stats = calculate_coherence_stats(baseline_feature_summaries, baseline_feature_ids)
finetuned_stats = calculate_coherence_stats(finetuned_feature_summaries)
finetuned_medical_stats = calculate_coherence_stats(finetuned_feature_summaries, finetuned_feature_ids)

# Function to print stats
def print_stats(name, stats):
    print(f"{name}:")
    print(f"  Mean (all): {stats['mean_all']:.4f}")
    print(f"  Median (all): {stats['median_all']:.4f}")
    print(f"  Mean (non-zero): {stats['mean_non_zero']:.4f}")
    print(f"  Median (non-zero): {stats['median_non_zero']:.4f}")
    print(f"  Fraction of non-zero scores: {stats['fraction_non_zero']:.2%}")

# Print stats for both models
print("Baseline gpt2-small:")
print_stats("All features", baseline_stats)
print_stats("Medical features", baseline_medical_stats)

print("\nFine-tuned gpt2-small:")
print_stats("All features", finetuned_stats)
print_stats("Medical features", finetuned_medical_stats)

Baseline gpt2-small:
All features:
  Mean (all): 0.0719
  Median (all): 0.0000
  Mean (non-zero): 0.2057
  Median (non-zero): 0.1399
  Fraction of non-zero scores: 38.82%
Medical features:
  Mean (all): 0.0644
  Median (all): 0.0000
  Mean (non-zero): 0.1998
  Median (non-zero): 0.1342
  Fraction of non-zero scores: 37.62%

Fine-tuned gpt2-small:
All features:
  Mean (all): 0.0728
  Median (all): 0.0246
  Mean (non-zero): 0.1470
  Median (non-zero): 0.1026
  Fraction of non-zero scores: 57.06%
Medical features:
  Mean (all): 0.0671
  Median (all): 0.0000
  Mean (non-zero): 0.1584
  Median (non-zero): 0.0938
  Fraction of non-zero scores: 47.12%


# Compute Coherence Scores From JSON

In [2]:
import json
import pandas as pd
import numpy as np
from scipy.spatial.distance import cosine
import gensim.downloader as api

In [3]:
# Load JSON data
with open('../features/features_medical_finetuned.json', 'r') as f:
    features_medical_finetuned = json.load(f)

with open('../features/features_medical_baseline.json', 'r') as f:
    features_medical_baseline = json.load(f)

with open('../features/features_all_finetuned.json', 'r') as f:
    features_all_finetuned = json.load(f)

with open('../features/features_all_baseline.json', 'r') as f:
    features_all_baseline = json.load(f)

In [5]:
# Load word embeddings
print("Loading GloVe embeddings...")
word_embeddings = api.load("glove-wiki-gigaword-100")
print("GloVe embeddings loaded.")

Loading GloVe embeddings...
GloVe embeddings loaded.


In [4]:
import re

def preprocess_token(token):
    # Remove 'Ġ' artifact and convert to lowercase
    token = token.lstrip('Ġ').lower()
    # Keep only alphabetic characters
    token = re.sub(r'[^a-z]', '', token)
    return token

def semantic_coherence_score(activated_tokens, activation_scores, word_embeddings, epsilon=1e-8):
    # Preprocess tokens and scores
    tokens_and_scores = [(preprocess_token(t), score) for t, score in zip(activated_tokens, activation_scores)]
    tokens_and_scores = [(t, score) for t, score in tokens_and_scores if t]  # Remove empty tokens

    # Get embeddings for each token
    token_embeddings = []
    weights = []
    for token, score in tokens_and_scores:
        if token in word_embeddings:
            token_embeddings.append(word_embeddings[token])
            weights.append(score)
        else:
            print(f"Warning: '{token}' not found in word embeddings")

    # If we have fewer than 2 valid tokens, return 0
    if len(token_embeddings) < 2:
        print(f"Warning: Fewer than 2 valid tokens for feature. Tokens: {activated_tokens}")
        return 0

    # Calculate weighted pairwise similarities
    similarities = []
    total_weight = 0
    for i in range(len(token_embeddings)):
        for j in range(i+1, len(token_embeddings)):
            sim = 1 - cosine(token_embeddings[i], token_embeddings[j])  # Cosine similarity
            weight = weights[i] * weights[j]  # Weight by product of activation scores
            similarities.append(sim * weight)
            total_weight += weight

    # Compute weighted average similarity
    score = np.sum(similarities) / (total_weight + epsilon)
    if score == 0:
        print(f"Warning: Zero score for feature. Tokens: {activated_tokens}")
    return score

In [6]:
def compute_coherence_scores(data, model_type, scope):
    # Compute coherence scores for each feature
    results = []
    for feature_id, feature_data in data.items():
        top_words = feature_data['top_words']
        activated_tokens = [word['word'].strip() for word in top_words]
        activation_scores = [word['activation'] for word in top_words]
        
        coherence_score = semantic_coherence_score(activated_tokens, activation_scores, word_embeddings)
        
        results.append({
            'feature_id': feature_id,
            'coherence_score': coherence_score,
            'top_words': ', '.join(activated_tokens[:5])  # Show top 5 words for brevity
        })

    # Create DataFrame
    df = pd.DataFrame(results)

    # Sort by coherence score in descending order
    df = df.sort_values('coherence_score', ascending=False)

    # Display top 10 features by coherence score
    print(df.head(10))

    # Display summary statistics
    print("\nSummary Statistics:")
    print(df['coherence_score'].describe())

    # Save results to CSV
    df.to_csv(f'../features/coherence_scores_{scope}_features_{model_type}.csv', index=False)
    print("\nResults saved to f'../features/coherence_scores_{scope}_features_{model_type}.csv'")
    return df

In [7]:
# coherence_scores_medical_baseline_df = compute_coherence_scores(features_medical_baseline, "medical", "baseline")
# coherence_scores_medical_finetuned_df = compute_coherence_scores(features_medical_finetuned, "medical", "finetuned")

coherence_scores_medical_baseline_df = compute_coherence_scores(features_all_baseline, "all", "baseline")
coherence_scores_medical_finetuned_df = compute_coherence_scores(features_all_finetuned, "all", "finetuned")

      feature_id  coherence_score  \
6130        6130              1.0   
15467      15467              1.0   
22287      22287              1.0   
10074      10074              1.0   
8895        8895              1.0   
8429        8429              1.0   
4093        4093              1.0   
5623        5623              1.0   
15734      15734              1.0   
8447        8447              1.0   

                                               top_words  
6130                    ign, igning, igned, IGN, ignment  
15467  Ġblockchain, ĠBlockchain, ĠEthereum, Ġcryptocu...  
22287                      ish, ishly, ISH, ishes, ished  
10074             ific, IFIC, ifice, ificial, ifications  
8895                   ishes, ishing, ished, ishers, ISH  
8429                ished, ishing, ishment, ishes, isher  
4093               ishing, ished, ishes, ishers, ishment  
5623                    igned, igning, ign, ignment, IGN  
15734                       ĠâĢĭ, âĢĭâĢĭ, âĢĭ, âĢİ, ĠâĢİ  
84

The output above indicates that there is a huge amount of tokens that do not have word embeddings in the glove model. Let's tally them up and compare against a few other word embedding models:

In [8]:
import gensim.downloader as api
from collections import Counter
import re

def preprocess_token(token):
    # Remove 'Ġ' artifact and convert to lowercase
    token = token.lstrip('Ġ').lower()
    # Keep only alphabetic characters
    token = re.sub(r'[^a-z]', '', token)
    return token

def evaluate_embedding_coverage(features_data, embedding_models):
    all_tokens = []
    for feature in features_data.values():
        all_tokens.extend([preprocess_token(word['word']) for word in feature['top_words']])
    
    # Remove empty strings and count unique tokens
    all_tokens = [token for token in all_tokens if token]
    unique_tokens = set(all_tokens)
    token_counts = Counter(all_tokens)
    
    results = {}
    for model_name, embeddings in embedding_models.items():
        missing_tokens = [token for token in unique_tokens if token not in embeddings]
        missing_count = sum(token_counts[token] for token in missing_tokens)
        
        results[model_name] = {
            'total_tokens': len(all_tokens),
            'unique_tokens': len(unique_tokens),
            'missing_unique_tokens': len(missing_tokens),
            'missing_total_tokens': missing_count,
            'coverage_unique': (len(unique_tokens) - len(missing_tokens)) / len(unique_tokens),
            'coverage_total': (len(all_tokens) - missing_count) / len(all_tokens),
            'most_common_missing': Counter(missing_tokens).most_common(10)
        }
    
    return results

# Load your feature data
import json
with open('../features/features_all_baseline.json', 'r') as f:
    features_data = json.load(f)

# Load embedding models
print("Loading word embedding models...")
embedding_models = {
    'glove-wiki-gigaword-100': api.load("glove-wiki-gigaword-100"),
    'word2vec-google-news-300': api.load("word2vec-google-news-300"),
    'fasttext-wiki-news-subwords-300': api.load("fasttext-wiki-news-subwords-300")
}
print("Word embedding models loaded.")

# Evaluate coverage
results = evaluate_embedding_coverage(features_data, embedding_models)

# Print results
for model_name, result in results.items():
    print(f"\nResults for {model_name}:")
    print(f"Total tokens: {result['total_tokens']}")
    print(f"Unique tokens: {result['unique_tokens']}")
    print(f"Missing unique tokens: {result['missing_unique_tokens']}")
    print(f"Missing total tokens: {result['missing_total_tokens']}")
    print(f"Coverage (unique): {result['coverage_unique']:.2%}")
    print(f"Coverage (total): {result['coverage_total']:.2%}")
    print("Most common missing tokens:")
    for token, count in result['most_common_missing']:
        print(f"  {token}: {count}")

Loading word embedding models...
[==================================================] 100.0% 1662.8/1662.8MB downloaded
[==================================================] 100.0% 958.5/958.4MB downloaded
Word embedding models loaded.

Results for glove-wiki-gigaword-100:
Total tokens: 234762
Unique tokens: 30174
Missing unique tokens: 5165
Missing total tokens: 34435
Coverage (unique): 82.88%
Coverage (total): 85.33%
Most common missing tokens:
  opian: 1
  effic: 1
  akeru: 1
  icle: 1
  disappro: 1
  rooft: 1
  inant: 1
  iration: 1
  anks: 1
  oppable: 1

Results for word2vec-google-news-300:
Total tokens: 234762
Unique tokens: 30174
Missing unique tokens: 6466
Missing total tokens: 42843
Coverage (unique): 78.57%
Coverage (total): 81.75%
Most common missing tokens:
  opian: 1
  tsarnaev: 1
  effic: 1
  akeru: 1
  icle: 1
  disappro: 1
  rooft: 1
  inant: 1
  iration: 1
  oppable: 1

Results for fasttext-wiki-news-subwords-300:
Total tokens: 234762
Unique tokens: 30174
Missing uniq

In [9]:
# Load your feature data
import json
with open('../features/features_medical_baseline.json', 'r') as f:
    features_data = json.load(f)

# ALREADY BE LOADED FROM ABOVE:
# Load embedding models
# print("Loading word embedding models...")
# embedding_models = {
#     'glove-wiki-gigaword-100': api.load("glove-wiki-gigaword-100"),
#     'word2vec-google-news-300': api.load("word2vec-google-news-300"),
#     'fasttext-wiki-news-subwords-300': api.load("fasttext-wiki-news-subwords-300")
# }
# print("Word embedding models loaded.")

# Evaluate coverage
results = evaluate_embedding_coverage(features_data, embedding_models)

# Print results
for model_name, result in results.items():
    print(f"\nResults for {model_name}:")
    print(f"Total tokens: {result['total_tokens']}")
    print(f"Unique tokens: {result['unique_tokens']}")
    print(f"Missing unique tokens: {result['missing_unique_tokens']}")
    print(f"Missing total tokens: {result['missing_total_tokens']}")
    print(f"Coverage (unique): {result['coverage_unique']:.2%}")
    print(f"Coverage (total): {result['coverage_total']:.2%}")
    print("Most common missing tokens:")
    for token, count in result['most_common_missing']:
        print(f"  {token}: {count}")


Results for glove-wiki-gigaword-100:
Total tokens: 1009
Unique tokens: 497
Missing unique tokens: 77
Missing total tokens: 101
Coverage (unique): 84.51%
Coverage (total): 89.99%
Most common missing tokens:
  ambul: 1
  xiety: 1
  antiv: 1
  immun: 1
  schizophren: 1
  hepat: 1
  microsc: 1
  veterin: 1
  steril: 1
  ferv: 1

Results for word2vec-google-news-300:
Total tokens: 1009
Unique tokens: 497
Missing unique tokens: 88
Missing total tokens: 110
Coverage (unique): 82.29%
Coverage (total): 89.10%
Most common missing tokens:
  ambul: 1
  xiety: 1
  antiv: 1
  immun: 1
  irus: 1
  schizophren: 1
  hepat: 1
  dsm: 1
  microsc: 1
  veterin: 1

Results for fasttext-wiki-news-subwords-300:
Total tokens: 1009
Unique tokens: 497
Missing unique tokens: 83
Missing total tokens: 103
Coverage (unique): 83.30%
Coverage (total): 89.79%
Most common missing tokens:
  ambul: 1
  xiety: 1
  antiv: 1
  immun: 1
  irus: 1
  schizophren: 1
  hepat: 1
  microsc: 1
  veterin: 1
  steril: 1


Let's check coverage across all three word embedding models:

In [10]:
import gensim.downloader as api
from collections import Counter
import re

def preprocess_token(token):
    token = token.lstrip('Ġ').lower()
    token = re.sub(r'[^a-z]', '', token)
    return token

def evaluate_combined_embedding_coverage(features_data, embedding_models):
    all_tokens = []
    for feature in features_data.values():
        all_tokens.extend([preprocess_token(word['word']) for word in feature['top_words']])
    
    all_tokens = [token for token in all_tokens if token]
    unique_tokens = set(all_tokens)
    token_counts = Counter(all_tokens)
    
    missing_tokens = set()
    for token in unique_tokens:
        if not any(token in model for model in embedding_models.values()):
            missing_tokens.add(token)
    
    missing_count = sum(token_counts[token] for token in missing_tokens)
    
    results = {
        'total_tokens': len(all_tokens),
        'unique_tokens': len(unique_tokens),
        'missing_unique_tokens': len(missing_tokens),
        'missing_total_tokens': missing_count,
        'coverage_unique': (len(unique_tokens) - len(missing_tokens)) / len(unique_tokens),
        'coverage_total': (len(all_tokens) - missing_count) / len(all_tokens),
        'most_common_missing': Counter(missing_tokens).most_common(10)
    }
    
    return results

# Load your feature data
import json
with open('../features/features_all_baseline.json', 'r') as f:
    features_all_baseline = json.load(f)
with open('../features/features_medical_baseline.json', 'r') as f:
    features_medical_baseline = json.load(f)

# Load embedding models
# print("Loading word embedding models...")
# embedding_models = {
#     'glove-wiki-gigaword-100': api.load("glove-wiki-gigaword-100"),
#     'word2vec-google-news-300': api.load("word2vec-google-news-300"),
#     'fasttext-wiki-news-subwords-300': api.load("fasttext-wiki-news-subwords-300")
# }
# print("Word embedding models loaded.")

# Evaluate combined coverage
results_all = evaluate_combined_embedding_coverage(features_all_baseline, embedding_models)
results_medical = evaluate_combined_embedding_coverage(features_medical_baseline, embedding_models)

# Print results
for name, results in [("All Features", results_all), ("Medical Features", results_medical)]:
    print(f"\nResults for {name}:")
    print(f"Total tokens: {results['total_tokens']}")
    print(f"Unique tokens: {results['unique_tokens']}")
    print(f"Missing unique tokens: {results['missing_unique_tokens']}")
    print(f"Missing total tokens: {results['missing_total_tokens']}")
    print(f"Coverage (unique): {results['coverage_unique']:.2%}")
    print(f"Coverage (total): {results['coverage_total']:.2%}")
    print("Most common missing tokens:")
    for token, count in results['most_common_missing']:
        print(f"  {token}: {count}")


Results for All Features:
Total tokens: 234762
Unique tokens: 30174
Missing unique tokens: 4169
Missing total tokens: 27293
Coverage (unique): 86.18%
Coverage (total): 88.37%
Most common missing tokens:
  andem: 1
  bsite: 1
  ossal: 1
  chenko: 1
  opian: 1
  ourney: 1
  illet: 1
  itizen: 1
  extermin: 1
  mopolitan: 1

Results for Medical Features:
Total tokens: 1009
Unique tokens: 497
Missing unique tokens: 70
Missing total tokens: 89
Coverage (unique): 85.92%
Coverage (total): 91.18%
Most common missing tokens:
  osterone: 1
  neurolog: 1
  amus: 1
  reatment: 1
  culosis: 1
  epile: 1
  antib: 1
  estones: 1
  ortality: 1
  abetes: 1


In [27]:
coherence_baseline_mean = coherence_baseline_df.coherence_score.mean()
coherence_ft_mean = coherence_ft_df.coherence_score.mean()

print(f'Coherence Baseline Mean = {coherence_baseline_mean}')
print(f'Coherence Finetuned Mean = {coherence_ft_mean}')
print(f'Mean Difference: {abs(coherence_baseline_mean - coherence_ft_mean)}')

Coherence Baseline Mean = 0.5437800812753218
Coherence Finetuned Mean = 0.351095164407496
Mean Difference: 0.19268491686782585


In [29]:
coherence_baseline_max = coherence_baseline_df.coherence_score.max()
coherence_baseline_min = coherence_baseline_df.coherence_score.min()

print(f'coherence baseline max: {coherence_baseline_max}')
print(f'coherence baseline min: {coherence_baseline_min}')

coherence_ft_max = coherence_ft_df.coherence_score.max()
coherence_ft_min = coherence_ft_df.coherence_score.min()

print(f'coherence ft max: {coherence_ft_max}')
print(f'coherence ft min: {coherence_ft_min}')

coherence baseline max: 0.7640679753864563
coherence baseline min: 0.11296098944869709
coherence ft max: 0.6793321548748883
coherence ft min: 0.06153612145227957


Normalizing the mean difference with respect to the min/max range is a good way to contextualize the difference. This will give a sense of how large the difference is relative to the overall range of coherence scores.

We can calculate the normalized mean difference as follows:

1. Calculate the range for both the baseline and fine-tuned coherence scores.
2. Take the average of these ranges.
3. Divide the mean difference by this average range.

In [30]:
# Calculate ranges
baseline_range = coherence_baseline_max - coherence_baseline_min
ft_range = coherence_ft_max - coherence_ft_min

# Calculate average range
avg_range = (baseline_range + ft_range) / 2

# Calculate mean difference
mean_diff = abs(coherence_baseline_mean - coherence_ft_mean)

# Calculate normalized mean difference
normalized_mean_diff = mean_diff / avg_range

print(f'Baseline Range: {baseline_range}')
print(f'Fine-tuned Range: {ft_range}')
print(f'Average Range: {avg_range}')
print(f'Normalized Mean Difference: {normalized_mean_diff}')

Baseline Range: 0.6511069859377592
Fine-tuned Range: 0.6177960334226087
Average Range: 0.6344515096801839
Normalized Mean Difference: 0.30370314189173414
